In [1]:
#增加边缘检测，雪的堆积

In [1]:
import cv2 as cv
import random
import numpy as np
import copy

In [18]:
capture = cv.VideoCapture(0)
time = 1
point_size = 1
point_color = (255, 255, 255)
thickness = 4
firstCreateFlag = True                                                                   #初始化雪花标记
while(True):
    isTrue,frame = capture.read()
    frame3=copy.deepcopy(frame)                                  #用深度拷贝保留原来3通道图
    
    #使用canny边缘检测#

    gray = cv.cvtColor(frame,cv.COLOR_BGR2GRAY)
    img1 = cv.GaussianBlur(gray,(3,3),0)
    frame = cv.Canny(img1, 100, 200)
    location = np.where(frame == 255)                           #获取边缘的位置
    x_loc=[]
    y_loc=[]
    for y in location[0]:
        y_loc.append(y)
    for x in location[1]:    
        x_loc.append(x)
    loclist = list(zip(x_loc,y_loc))
    
    #雪花效果#
    
    print("第 "+str(time)+"  次")
    if(firstCreateFlag):                                                #初始化雪花点
        count=50                                                        #初始雪花个数
        speedstart = 10                                                #下雪速度
        speednow = 0
        addcount = 50                                               #增加雪量
        probability = 0.9                                            #雪花可以穿过边缘与形成堆积的概率，以避免雪花只停留在最上面的边缘
        x_list = []
        y_list = [0]*count
        x_accumulate = []
        y_accumulate = []
        apexlist = []
        
        n=0
        while(n<count):
            x_list.append(random.randint(0,frame.shape[1]))#随机生成x值
            n+=1
        xy_list = list(zip(x_list,y_list))
        firstCreateFlag = False
        print("     生成的xy_list"+str(xy_list))
    else:                                                               #增加雪花点
        speednow += speedstart
        if(speednow%(5*speedstart) == 0):                                 #控制增加的速度，并非每读一帧就增加雪花
            count += addcount
            n = 0
            while(n<(addcount)):
                x_item.append(random.randint(0,frame.shape[1]))
                y_item.append(0)
                n+=1
            xy_list = list(zip(x_item,y_item))
            speednow = speedstart
            print("     增加雪花生成的xy_list"+str(xy_list))


    
    y_add_list = []
    x_add_list = []
    n=0
    while(n<count):                                              #随机生成x,y增量，x用于左右飘动，y用于向下飘动
        y_add_list.append(random.randint(int(speedstart/2),speedstart))
        x_add_list.append(random.randint(-5,5))
        n+=1

    
    i = 0
    x_item = []
    y_item = []
    subcount = 0
    if(time%(4*addcount) == 0):                           #模拟雪融化
        x_accumulate = x_accumulate[int(len(x_accumulate)/(1.5)):]
        y_accumulate = y_accumulate[int(len(y_accumulate)/(1.5)):]
        apexlist = apexlist[int(len(apexlist)/(speedstart*addcount / 150)):]
    print("     生成的apexlist"+str(apexlist))



    for x,y in xy_list:                                                              #将增量运用到上一个x，y
        notEdgeFlag  = True                                                    #雪花未到达边缘标记
        if(y+y_add_list[i] > frame.shape[0]):                               #超出下框的雪花点删除，避免list数组越来越大
            subcount += 1
            i+=1
            continue
        else:
            if(random.random() > probability):
                for x_location,y_location in loclist:                         #雪花在边缘位置堆积，或以一定概率穿过
                    if((((y+y_add_list[i]) > y_location) and ((x+x_add_list[i])==x_location))):
                        y_accumulate.append(y_location)
                        x_accumulate.append(x_location)
                        apexlist.append((x_location,y_location-1))        #已堆积雪花也算作边缘位置，制造雪可以堆成尖的效果
                        notEdgeFlag  = False
                        subcount += 1
                        break
                apexHigh = 0                                                       #一帧画面时间内有多少点可以堆积
                for x_location,y_location in apexlist:                       #检查是否可堆积，需要下雪速度与雪量乘积达到一定范围才有可能
                    if((((y+y_add_list[i]) > y_location) and ((x+x_add_list[i])==x_location) and (speedstart*addcount >= 100))):
                        if((random.random() > probability) ):
                            apexHigh += 1
                            apexlist.append((x_location,y_location-apexHigh))
                            break
                        
        if(notEdgeFlag):                                                          #没有超过下框，且没有在边缘位置
            y_item.append(y+y_add_list[i])         
            x_item.append(x+x_add_list[i])
        i+=1
    count-=subcount

    
    #组合生成新的点，与堆积列表#
    xy_list = list(zip(x_item,y_item))
    xy_accumulatelist = list(zip(x_accumulate,y_accumulate))
    print("     xy_accumulatelist"+str(xy_accumulatelist))
    print("     xy_list"+str(xy_list))
    for xy in xy_list+xy_accumulatelist+apexlist:
        cv.circle(frame3, xy, point_size, point_color, thickness)     #在原来3通道图上画圈
    
    cv.imshow("test",frame3)
    time+=1
    if(cv.waitKey(1) & 0xFF == ord("s")):
        break
        
capture.release()
cv.destroyAllWindows()

第 1  次
     生成的xy_list[(511, 0), (308, 0), (183, 0), (326, 0), (99, 0), (541, 0), (142, 0), (395, 0), (633, 0), (59, 0), (194, 0), (348, 0), (532, 0), (545, 0), (481, 0), (143, 0), (71, 0), (42, 0), (5, 0), (249, 0), (165, 0), (516, 0), (245, 0), (239, 0), (40, 0), (388, 0), (329, 0), (42, 0), (474, 0), (73, 0), (364, 0), (340, 0), (612, 0), (91, 0), (417, 0), (135, 0), (591, 0), (257, 0), (375, 0), (55, 0), (270, 0), (394, 0), (326, 0), (101, 0), (274, 0), (292, 0), (299, 0), (511, 0), (29, 0), (577, 0)]
     生成的apexlist[]
     xy_accumulatelist[]
     xy_list[(506, 5), (307, 10), (182, 7), (327, 10), (101, 8), (545, 10), (146, 8), (398, 8), (632, 10), (61, 5), (189, 8), (347, 8), (534, 5), (543, 5), (486, 5), (140, 9), (72, 8), (45, 8), (8, 9), (254, 9), (165, 5), (517, 7), (240, 6), (242, 8), (35, 8), (393, 6), (326, 7), (37, 10), (476, 6), (72, 9), (361, 8), (335, 8), (610, 9), (87, 7), (417, 10), (136, 9), (586, 10), (252, 6), (380, 7), (56, 5), (266, 5), (397, 10), (331, 8), (106

第 12  次
     生成的apexlist[]
     xy_accumulatelist[]
     xy_list[(505, 87), (294, 92), (185, 80), (334, 89), (100, 94), (557, 101), (145, 87), (383, 95), (632, 94), (58, 89), (202, 93), (351, 93), (536, 88), (542, 94), (483, 92), (123, 93), (87, 85), (50, 99), (-2, 92), (262, 90), (166, 82), (523, 87), (239, 98), (236, 91), (38, 93), (387, 88), (327, 91), (48, 96), (481, 96), (76, 88), (374, 89), (346, 90), (589, 88), (85, 95), (423, 96), (120, 97), (591, 92), (261, 80), (379, 96), (52, 78), (292, 92), (409, 97), (326, 89), (105, 82), (254, 86), (275, 91), (304, 92), (523, 83), (29, 78), (563, 85), (458, 55), (505, 46), (159, 54), (196, 55), (319, 52), (524, 49), (414, 55), (566, 57), (398, 50), (344, 54), (106, 54), (633, 45), (236, 55), (274, 59), (616, 54), (38, 53), (509, 45), (125, 57), (602, 45), (394, 54), (410, 56), (374, 55), (602, 51), (475, 46), (153, 51), (541, 48), (185, 56), (328, 55), (318, 49), (384, 52), (478, 53), (253, 57), (493, 49), (207, 58), (191, 51), (86, 58), 

第 18  次
     增加雪花生成的xy_list[(502, 124), (292, 123), (189, 117), (343, 126), (99, 133), (560, 138), (136, 126), (376, 138), (623, 127), (57, 129), (200, 131), (349, 131), (542, 128), (550, 130), (485, 122), (116, 130), (75, 123), (40, 142), (-7, 133), (255, 131), (164, 123), (526, 125), (234, 134), (242, 125), (43, 131), (377, 124), (320, 127), (56, 132), (474, 136), (70, 129), (385, 128), (342, 128), (594, 120), (86, 133), (422, 130), (113, 132), (599, 128), (262, 121), (376, 136), (55, 122), (299, 132), (417, 136), (326, 125), (99, 124), (244, 119), (277, 124), (306, 131), (512, 122), (26, 110), (565, 123), (457, 92), (512, 83), (162, 93), (189, 90), (331, 94), (516, 84), (399, 99), (570, 95), (398, 83), (349, 93), (119, 91), (630, 76), (252, 94), (264, 90), (611, 90), (35, 93), (500, 79), (115, 96), (596, 90), (380, 87), (412, 91), (378, 94), (609, 88), (471, 83), (151, 90), (534, 90), (179, 99), (335, 87), (316, 91), (384, 86), (484, 94), (250, 94), (503, 85), (198, 95), (190, 85), 

第 21  次
     生成的apexlist[]
     xy_accumulatelist[]
     xy_list[(490, 156), (293, 156), (190, 146), (339, 161), (92, 160), (545, 166), (139, 157), (376, 167), (625, 155), (56, 153), (197, 159), (346, 160), (535, 162), (555, 161), (499, 153), (115, 164), (65, 155), (43, 168), (-12, 161), (257, 161), (174, 151), (526, 148), (237, 168), (239, 154), (39, 157), (379, 155), (327, 158), (46, 170), (466, 164), (81, 158), (375, 156), (339, 161), (597, 150), (88, 167), (419, 161), (116, 163), (594, 161), (257, 155), (372, 168), (46, 150), (301, 161), (415, 166), (312, 152), (91, 156), (242, 153), (284, 157), (304, 163), (519, 147), (17, 141), (569, 150), (450, 117), (510, 109), (158, 122), (189, 119), (321, 125), (510, 109), (412, 128), (571, 124), (400, 110), (356, 126), (124, 122), (630, 103), (257, 124), (274, 117), (606, 124), (36, 120), (492, 111), (115, 124), (599, 116), (384, 116), (408, 119), (383, 125), (602, 116), (470, 113), (154, 121), (532, 115), (177, 131), (336, 114), (301, 117),

     xy_accumulatelist[]
     xy_list[(483, 175), (300, 169), (196, 160), (337, 179), (96, 179), (544, 180), (139, 171), (373, 178), (621, 170), (59, 168), (192, 178), (353, 176), (536, 179), (556, 178), (495, 168), (114, 178), (60, 168), (39, 186), (-14, 179), (257, 177), (181, 169), (520, 165), (239, 188), (239, 171), (35, 167), (383, 169), (320, 172), (45, 186), (471, 182), (79, 172), (374, 170), (348, 179), (599, 166), (92, 180), (420, 177), (111, 179), (603, 171), (262, 172), (372, 181), (52, 165), (307, 176), (420, 182), (315, 165), (95, 175), (241, 172), (279, 170), (308, 182), (521, 161), (11, 161), (559, 163), (457, 131), (503, 125), (161, 137), (189, 133), (320, 142), (513, 121), (417, 142), (568, 135), (404, 125), (361, 136), (117, 139), (622, 118), (250, 139), (273, 130), (611, 139), (43, 137), (492, 123), (112, 140), (590, 132), (381, 128), (412, 133), (382, 139), (607, 129), (466, 127), (153, 134), (523, 133), (173, 144), (335, 129), (301, 128), (392, 128), (477, 137), (2

...

     xy_accumulatelist[(43, 210), (148, 211), (110, 211), (541, 369), (309, 211), (67, 211), (52, 211), (71, 211), (332, 211), (467, 212), (427, 212), (80, 211), (214, 261), (150, 211), (204, 261), (220, 274), (372, 212), (236, 211), (89, 211), (280, 211), (81, 211), (603, 325), (431, 212), (60, 211), (76, 211), (349, 212), (409, 211), (215, 261), (110, 211), (78, 211), (242, 211), (372, 211), (478, 212), (251, 211), (595, 212), (622, 212), (92, 211), (183, 211), (611, 211), (277, 212), (108, 211), (20, 210), (302, 211), (6, 211), (36, 210), (476, 212), (414, 212), (181, 211), (483, 212), (173, 211), (442, 211), (459, 212), (53, 211), (91, 211), (495, 212), (598, 327), (580, 327), (582, 328), (410, 211), (461, 211), (15, 210), (443, 211), (478, 211), (342, 211), (206, 260), (473, 211), (333, 212), (527, 304), (353, 211), (346, 212), (394, 212), (98, 210), (249, 211), (76, 211), (231, 230), (488, 211), (258, 211), (350, 212), (479, 212), (378, 211), (526, 303), (361, 212), (534, 374), (

     xy_accumulatelist[(43, 210), (148, 211), (110, 211), (541, 369), (309, 211), (67, 211), (52, 211), (71, 211), (332, 211), (467, 212), (427, 212), (80, 211), (214, 261), (150, 211), (204, 261), (220, 274), (372, 212), (236, 211), (89, 211), (280, 211), (81, 211), (603, 325), (431, 212), (60, 211), (76, 211), (349, 212), (409, 211), (215, 261), (110, 211), (78, 211), (242, 211), (372, 211), (478, 212), (251, 211), (595, 212), (622, 212), (92, 211), (183, 211), (611, 211), (277, 212), (108, 211), (20, 210), (302, 211), (6, 211), (36, 210), (476, 212), (414, 212), (181, 211), (483, 212), (173, 211), (442, 211), (459, 212), (53, 211), (91, 211), (495, 212), (598, 327), (580, 327), (582, 328), (410, 211), (461, 211), (15, 210), (443, 211), (478, 211), (342, 211), (206, 260), (473, 211), (333, 212), (527, 304), (353, 211), (346, 212), (394, 212), (98, 210), (249, 211), (76, 211), (231, 230), (488, 211), (258, 211), (350, 212), (479, 212), (378, 211), (526, 303), (361, 212), (534, 374), (

     xy_accumulatelist[(43, 210), (148, 211), (110, 211), (541, 369), (309, 211), (67, 211), (52, 211), (71, 211), (332, 211), (467, 212), (427, 212), (80, 211), (214, 261), (150, 211), (204, 261), (220, 274), (372, 212), (236, 211), (89, 211), (280, 211), (81, 211), (603, 325), (431, 212), (60, 211), (76, 211), (349, 212), (409, 211), (215, 261), (110, 211), (78, 211), (242, 211), (372, 211), (478, 212), (251, 211), (595, 212), (622, 212), (92, 211), (183, 211), (611, 211), (277, 212), (108, 211), (20, 210), (302, 211), (6, 211), (36, 210), (476, 212), (414, 212), (181, 211), (483, 212), (173, 211), (442, 211), (459, 212), (53, 211), (91, 211), (495, 212), (598, 327), (580, 327), (582, 328), (410, 211), (461, 211), (15, 210), (443, 211), (478, 211), (342, 211), (206, 260), (473, 211), (333, 212), (527, 304), (353, 211), (346, 212), (394, 212), (98, 210), (249, 211), (76, 211), (231, 230), (488, 211), (258, 211), (350, 212), (479, 212), (378, 211), (526, 303), (361, 212), (534, 374), (

     xy_accumulatelist[(43, 210), (148, 211), (110, 211), (541, 369), (309, 211), (67, 211), (52, 211), (71, 211), (332, 211), (467, 212), (427, 212), (80, 211), (214, 261), (150, 211), (204, 261), (220, 274), (372, 212), (236, 211), (89, 211), (280, 211), (81, 211), (603, 325), (431, 212), (60, 211), (76, 211), (349, 212), (409, 211), (215, 261), (110, 211), (78, 211), (242, 211), (372, 211), (478, 212), (251, 211), (595, 212), (622, 212), (92, 211), (183, 211), (611, 211), (277, 212), (108, 211), (20, 210), (302, 211), (6, 211), (36, 210), (476, 212), (414, 212), (181, 211), (483, 212), (173, 211), (442, 211), (459, 212), (53, 211), (91, 211), (495, 212), (598, 327), (580, 327), (582, 328), (410, 211), (461, 211), (15, 210), (443, 211), (478, 211), (342, 211), (206, 260), (473, 211), (333, 212), (527, 304), (353, 211), (346, 212), (394, 212), (98, 210), (249, 211), (76, 211), (231, 230), (488, 211), (258, 211), (350, 212), (479, 212), (378, 211), (526, 303), (361, 212), (534, 374), (

     xy_accumulatelist[(43, 210), (148, 211), (110, 211), (541, 369), (309, 211), (67, 211), (52, 211), (71, 211), (332, 211), (467, 212), (427, 212), (80, 211), (214, 261), (150, 211), (204, 261), (220, 274), (372, 212), (236, 211), (89, 211), (280, 211), (81, 211), (603, 325), (431, 212), (60, 211), (76, 211), (349, 212), (409, 211), (215, 261), (110, 211), (78, 211), (242, 211), (372, 211), (478, 212), (251, 211), (595, 212), (622, 212), (92, 211), (183, 211), (611, 211), (277, 212), (108, 211), (20, 210), (302, 211), (6, 211), (36, 210), (476, 212), (414, 212), (181, 211), (483, 212), (173, 211), (442, 211), (459, 212), (53, 211), (91, 211), (495, 212), (598, 327), (580, 327), (582, 328), (410, 211), (461, 211), (15, 210), (443, 211), (478, 211), (342, 211), (206, 260), (473, 211), (333, 212), (527, 304), (353, 211), (346, 212), (394, 212), (98, 210), (249, 211), (76, 211), (231, 230), (488, 211), (258, 211), (350, 212), (479, 212), (378, 211), (526, 303), (361, 212), (534, 374), (